In [1]:
import json
import numpy as np
import pandas as pd
import pickle
import copy

In [2]:
rating_df = pd.read_csv('./ratings.dat', sep='::', names=["userId", "itemId", "rating", "timestamp"], engine='python')
rating_df.drop(columns=['timestamp'], inplace=True)
rating_df.drop(columns=['rating'], inplace=True)
rating_df.head()

userId  itemId
0       1    1193
1       1     661
2       1     914
3       1    3408
4       1    2355

In [3]:
item_df = pd.read_csv('./movies.dat', sep='::', names=['itemId', 'title', 'genres'], engine='python', encoding='latin-1')
item_df.head()

itemId                               title                        genres
0       1                    Toy Story (1995)   Animation|Children's|Comedy
1       2                      Jumanji (1995)  Adventure|Children's|Fantasy
2       3             Grumpier Old Men (1995)                Comedy|Romance
3       4            Waiting to Exhale (1995)                  Comedy|Drama
4       5  Father of the Bride Part II (1995)                        Comedy

In [4]:
item_genre_dict = dict()
for i in range(len(item_df)):
    genre_str = item_df.at[i, 'genres']
    genre_list = genre_str.split('|')
    item_genre_dict[item_df.at[i, 'itemId']] = genre_list
    
# dictionary mapping itemId - Genre List
item_genre_dict

{1: ['Animation', "Children's", 'Comedy'],
 2: ['Adventure', "Children's", 'Fantasy'],
 3: ['Comedy', 'Romance'],
 4: ['Comedy', 'Drama'],
 5: ['Comedy'],
 6: ['Action', 'Crime', 'Thriller'],
 7: ['Comedy', 'Romance'],
 8: ['Adventure', "Children's"],
 9: ['Action'],
 10: ['Action', 'Adventure', 'Thriller'],
 11: ['Comedy', 'Drama', 'Romance'],
 12: ['Comedy', 'Horror'],
 13: ['Animation', "Children's"],
 14: ['Drama'],
 15: ['Action', 'Adventure', 'Romance'],
 16: ['Drama', 'Thriller'],
 17: ['Drama', 'Romance'],
 18: ['Thriller'],
 19: ['Comedy'],
 20: ['Action'],
 21: ['Action', 'Comedy', 'Drama'],
 22: ['Crime', 'Drama', 'Thriller'],
 23: ['Thriller'],
 24: ['Drama', 'Sci-Fi'],
 25: ['Drama', 'Romance'],
 26: ['Drama'],
 27: ['Drama'],
 28: ['Romance'],
 29: ['Adventure', 'Sci-Fi'],
 30: ['Drama'],
 31: ['Drama'],
 32: ['Drama', 'Sci-Fi'],
 33: ['Adventure', 'Romance'],
 34: ["Children's", 'Comedy', 'Drama'],
 35: ['Drama', 'Romance'],
 36: ['Drama'],
 37: ['Documentary'],
 38: ['C

In [5]:
print(len(rating_df))
rating_df.drop_duplicates(subset =['itemId', 'userId'], 
                          keep = 'first', inplace = True)
print(len(rating_df))

1000209
1000209


In [6]:
item_set = set(rating_df['itemId'].unique())
user_set = set(rating_df['userId'].unique())
print('item num = ' + str(len(item_set)))
print('user num = ' + str(len(user_set)))

item num = 3706
user num = 6040


In [7]:
# count the number for each genre and sort
import operator
genre_count = dict()
for l in item_genre_dict:
    for g in item_genre_dict[l]:
        if not g in genre_count:
            genre_count[g] = 1
        else:
            genre_count[g] += 1

genre_count_sorted = sorted(genre_count.items(), key=operator.itemgetter(1), reverse=True)
genre_count_sorted

[('Drama', 1603),
 ('Comedy', 1200),
 ('Action', 503),
 ('Thriller', 492),
 ('Romance', 471),
 ('Horror', 343),
 ('Adventure', 283),
 ('Sci-Fi', 276),
 ("Children's", 251),
 ('Crime', 211),
 ('War', 143),
 ('Documentary', 127),
 ('Musical', 114),
 ('Mystery', 106),
 ('Animation', 105),
 ('Fantasy', 68),
 ('Western', 68),
 ('Film-Noir', 44)]

In [8]:
rating_df.reset_index(drop=True, inplace=True)
rdf_backup = copy.copy(rating_df)

In [9]:
rdf = copy.copy(rdf_backup)

In [10]:
# iteratively remove items and users with less than 10 reviews
rdf['user_freq'] = rdf.groupby('userId')['userId'].transform('count')
rdf['item_freq'] = rdf.groupby('itemId')['itemId'].transform('count')
while np.min(rdf['user_freq']) <= 9:
    rdf.drop(rdf.index[rdf['user_freq'] <= 9], inplace=True)
    rdf.reset_index(drop=True, inplace=True)
    rdf['item_freq'] = rdf.groupby('itemId')['itemId'].transform('count')
    rdf.drop(rdf.index[rdf['item_freq'] <= 9], inplace=True)
    rdf.reset_index(drop=True, inplace=True)
    rdf['user_freq'] = rdf.groupby('userId')['userId'].transform('count')
    rdf.reset_index(drop=True, inplace=True)

In [11]:
item_list = rdf['itemId'].unique()
user_list = rdf['userId'].unique()
print('item num = ' + str(len(item_list)))
print('user num = ' + str(len(user_list)))

item num = 3706
user num = 6040


In [12]:
rdf.head()

userId  itemId  user_freq  item_freq
0       1    1193         53       1725
1       1     661         53        525
2       1     914         53        636
3       1    3408         53       1315
4       1    2355         53       1703

In [13]:
# get the user and item str id->int id dict
i = 0
user_old2new_id_dict = dict()
for u in user_list:
    if not u in user_old2new_id_dict:
        user_old2new_id_dict[u] = i
        i += 1
j = 0
item_old2new_id_dict = dict()
for i in item_list:
    if not i in item_old2new_id_dict:
        item_old2new_id_dict[i] = j
        j += 1

In [14]:
# Update old ids to new ids to make sure ids are contiguous
# print(user_old2new_id_dict)
# print(item_old2new_id_dict)

In [15]:
print('sparsity: ' + str(len(rdf) * 1.0 / (len(user_list) * len(item_list))))

sparsity: 0.044683625622312845


In [16]:
# convert the str id of items in item_df to int id
for i in range(len(item_df)):
    if item_df.at[i, 'itemId'] not in item_old2new_id_dict:
        item_df.drop([i], axis=0, inplace=True)
    else:
        item_df.at[i, 'itemId'] = item_old2new_id_dict[item_df.at[i, 'itemId']]

In [17]:
# get df for rdf with int id for user and item
for i in range(len(rdf)):
    rdf.at[i, 'userId'] = user_old2new_id_dict[rdf.at[i, 'userId']]
    rdf.at[i, 'itemId'] = item_old2new_id_dict[rdf.at[i, 'itemId']]
item_list = rdf['itemId'].unique()
user_list = rdf['userId'].unique()

In [18]:
# get the df of train, vali, and test df
rdf.reset_index(inplace=True, drop=True)
train_df = rdf.copy()

train_ratio = 0.7
vali_ratio = 0.1
test_ratio = 0.2

vali_size = int(vali_ratio * len(rdf))
test_size = int(test_ratio * len(rdf))

vali_idx = np.random.choice(np.arange(len(train_df)), 
                            vali_size,
                            replace=False).tolist()
vali_df = train_df.copy()
vali_df = vali_df.loc[vali_idx]
train_df.drop(vali_idx, axis=0, inplace=True)
train_df.reset_index(drop=True, inplace=True)

test_idx = np.random.choice(np.arange(len(train_df)), 
                            test_size,
                            replace=False).tolist()
test_df = train_df.copy()
test_df = test_df.loc[test_idx]
train_df.drop(test_idx, axis=0, inplace=True)

train_df.reset_index(drop=True, inplace=True)
test_df.reset_index(drop=True, inplace=True)
vali_df.reset_index(drop=True, inplace=True)
train_df.head()

userId  itemId  user_freq  item_freq
0       0       1         53        525
1       0       3         53       1315
2       0       7         53       1352
3       0       8         53        763
4       0      10         53       1060

In [19]:
# compute the popularity of items, stored in item_df
item_pop = np.array(train_df['itemId'].value_counts())
item_pop_id = np.array(train_df['itemId'].value_counts().index)
item_df['pop'] = 0
for i in range(len(item_pop_id)):
    item_df.at[item_df['itemId'] == item_pop_id[i], 'pop'] = item_pop[i]


In [20]:
train_df.drop(columns=['user_freq', 'item_freq'], inplace=True)
test_df.drop(columns=['user_freq', 'item_freq'], inplace=True)
vali_df.drop(columns=['user_freq', 'item_freq'], inplace=True)

In [21]:
train_df.reset_index(drop=True, inplace=True)
test_df.reset_index(drop=True, inplace=True)
vali_df.reset_index(drop=True, inplace=True)

In [22]:
# generate list of items users like in train, vali, test sets for each user

num_item = len(item_list)
num_user = len(user_list)

user_train_like = []
user_test_like = [] 
user_vali_like = []  

train_array = train_df[['userId', 'itemId']].values
vali_array = vali_df[['userId', 'itemId']].values
test_array = test_df[['userId', 'itemId']].values

for u in user_list:
    train_like = (train_array[list(np.where(train_array[:, 0] == u)[0]), 1]).astype(int)
    vali_like = (vali_array[list(np.where(vali_array[:, 0] == u)[0]), 1]).astype(int)
    test_like = (test_array[list(np.where(test_array[:, 0] == u)[0]), 1]).astype(int)
    print(train_like, vali_like, test_like)
    user_train_like.append(train_like)
    user_vali_like.append(vali_like)
    user_test_like.append(test_like)
    
np.save('./user_train_like.npy', np.array(user_train_like))
np.save('./user_vali_like.npy', np.array(user_vali_like))
np.save('./user_test_like.npy', np.array(user_test_like))
    

[ 1  3  7  8 10 11 12 14 16 17 18 21 24 25 26 27 29 31 32 34 35 36 37 38
 39 40 41 42 44 45 48 51 52] [49 30 47  4 28] [15 43 19 20 50 23 33  2  5  6  0 13 46  9 22]
[ 53  55  56  57  58  59  61  62  65  66  67  68  69  70  18  73  74  75
  77  78  79  80  82  84  85  86  87  88  90  91  92  93  94  95  96  97
  98  99 100 101 102 103 104  48 106 107 108 109 110 111 112 113 114 115
   0 118 122 123 124 125 126 127 128 129 130 131 132 134 137 138 139 140
 142 143 144 145 146  20 148 149 151 152 153 154 155 158 159 160 161 162
 163 164 166 167  47 169 171 172  52 173] [ 83 116 174  81  60 133 168 165  89 156] [120  54  42 105 141  64  71 136  63 119 117  72 170 121 147 150 135  76
 157]
[175 176 177 178 179 180  64 181 182 183 184  84 187 188 189 190  44 191
 193 116 194 195 124 123   5 127 196 197 198 199 200 201 202  41 204 168
 207] [ 22  58 205 104] [185 206 192 203  50 113 186 166   4 128]
[ 63  64 209 210 113 124 127  26 156 211 212 213 215 216 217] [208  43] [ 48  44 139 214]
[219

[ 218   56 2353 1175  555 1709 2320  558  182  560  561 2158  240  872
 1115  567 2404  875 1239  876  255 1610  577 1535  110  115  116  518
  194    0  195  265  124  123  126  127 1029 1241  587  128  396 2405
 1301  523   22 1340  794 1041  597  600  296 1185 2332 1901 1496 2406
  529 1344    6 2407  312  799 1471 1251  534  316   18 2075   80  625
   82 1906 1253 1448  887   87  633  321 1545 1551 2008 1352 1258 1304
  117 1195 1711  420 1196  645  648  197 2080 1200  153  506 1555 1501
  662  665  669 2030 1832 1072  675  385 2410  676 1714 1376 1271 1204
  895 2411   57   59  226  437 1666  832 1210 2412 1274 1275   78   81
 1780  392 2413 1387  393 1388 1670 2249   93 1637 1687  688  451 1310
  120  905  125 1691    4  455 1509  990  693  458  694 1454  149 2415
 1150 1403  908  280  706 2057  283  201 1151  941  719 1701  723  176
  302 2416  733 1222  735 1600  736  537 1703   89 1601   90 2418 1602
  189   92 1225  748 1603 2093  486 2094  324  913  857  102  493 2367
 2095 

[ 237 1244   86    4  993    3 1171  519  790  267  526  885  499 1712
  376  387   68  406  331 1229] [104 340 952  64] [1232  231  853  545  860  113  259]
[1326 1328   97  573 1484  256 2913 1485  124 2141 1341 1343  831  528
  612  312 2343   74 2795  318  630 1828 1908 2134  418  119 2080  542
 2914  506  155  896   86  452  268  458 2189  524  703  907  470  472
  474 2091  480  732 1416  530   27 1929   89  189   31  324  538  488
  341  921 1934  926  509 1013  371  551   60 1526  438 1331  564  873
  568   39 2915  519  267 1028  454  132 1030  457  792  590 1941  461
 2281  603  164  167 1655 2736 2138 1188 1190 2139  635 1058 1256  109
 1259 1487 1712 1063  356  501  359  504 1065 2916  372   41  809  168
  378  381  387   68 1209  514  244  685 2599  464   23 1401  704  163
  527  721   51  738   64  533  317 1097 1099  326   48 1674 2051  545
 1586   26 2918 1109 2454  837  380   52] [2056 1302 2659   10  508  160  237  293   44  288 1332  280 1303   92
 2917 2033   56  75

[ 128 1905  411  669 2362 2982  486 3088 1486  372  104   64 2011 1434
  174] [ 553 1586  434] [1633 1023  381 1106  280   67  831]
[ 182 1165  566  567   33   40  450 2067  256  576  577 1176  116  124
  123  126  587  128 1301 1038 2141 1340  597  599  285 1180   29  608
 1045  609 1617 1826  797  316  864 1761 1906  632 1544 1765 1551 1351
 1352 1258 1195  420  645  197    9  426  661 1364 1465  669 1631  385
  811 1378   55  679  437  896  983   85 1635 1393  690  129 1150  280
 1513 1405  941 1152  472  400  726  176  731 1415  733  305  734 1737
  484  537  319  189  487  323  538  825  423  134   12  509  371 1520
 1526  552  553 1331 1531 1024 1315  520  521  399  158  880  162  604
  164 2220    7  614 1049 1050 1051 1052  621 2041 1194 1056  635 1623
 1256 1059  491  639  416 2043  352  140 1357  502 2153   41   45   46
  674  168  171  382 1596  386   13   14 2251  244  686  814 1864  815
 1865  138  695 1083  699  701 1598 1571   19  704 1404  166  527  727
   51  475  737 

[2898 3151  237  184   84   97 1177  517  128    8   10 2694   22  467
 1041  600  296  207 2272  797  864  628  418    9  542 1200 2081  668
 1629  675  385 1211 2344  269 2896   30 1221  537 1005  322 1425 1931
  340 3152 1010  428 1230   60 2519 2170  793  141  958    7  614 2610
 1887   44 1059  541  499  651 1855  352 3153  357 1634  244  104  138
 1570  151  206  532 2729 1456  113  767  834  547 1998 1016   58  949
  556  182  561 3154  577 1176  582 1027  584    1  127 1241 1034 1040
  599  173 2474  831   75  642  646  196  806  155   85  444 1310  524
   32  941 2091  480  730  732  734  432  179 2018  857  488  345  922
  762  788  251  790  454  273 1125 1247  290 1050  618  315 2920  635
  198  354  657  364   37   45   46  168  979 1308   62 1383 1390  259
 3155   15 1216 1218   19  711 1280  713  714  715  718  994 1087 2891
  737  738   64 1157  406   67  741  317  745  183 2125  756 1676  365
   26  172 1018  384] [1488  869  243 1499  840  976 1650  939 1734 1596  176

...

[ 237  567   40 1118  396 1538  864 1200 1393  690    3  200 1230  572
   44 1854  386 2237  277 2241  326 2056  312  622   50  335  642  678
 1691 1150  189  748 1013  132  290  291  167 1262  198  657  807  221
   13   68  390  514  687  264 1149  714   47 1228 1105  828 1328  517
  116  195   22  283   30  537  509  775 1526  438 1163  840 1887  352
   16 1674    4  280  735   27  350  243  788   39  454  273  954  880
   38  511  900   14  210 1216   23  715  717 1157   48  419  837] [ 104    7  160  127  587  155  470   15   60  465   64 1487 1176  214
 2283  681  558  532  134] [1593  186  541   19   97   41   58 1101  124  119  533  171 1431  437
 1524 1935   92  737  148  317  618  699 2170  322  899 1712  673  663]
[ 567   97  876  110  396   82  418  338 1770  849  690 1785  122  268
 2154 1790    3  340 2331  156 1442  776 1322 3300 1592  515 1654 1338
  796 1058  109  416 1063 1381   79  982 2263  248  104 2174   69 1989
   58 1528   88   75 1681   50 1625  368 1691 1084  4

[1334 1448  540  422 1033  104   50   55 1691  189 2145  290  803  171
  382  247  116  246  176 1346 1801  534  129  474  323  134  164  183] [ 88 769] [381]
[ 875 1334  794  401  648 1200  392  690 1145 1649 2884 1059  109  656
  845  104 2237  912  942 2847 1471  622 2134 2245 1691  733  391  519
 1613 2351  198 1712 1964  425 1366  429 2958   68  992 1154  944   60
 1935 1346 1960  541  349 1068 1069  975 1071   99 1578  407  409  742
 1422 1428 1674  112 2634  644 2091 2239  860  454 1593  635  211  666
 1067 1662 1306   38 1644] [ 979 1419  695 1854 1634 1418    3  664  178 3020 2498 1254] [ 405  277  897  697  522  327  544 2619  876  499  465  203]
[1177 2332  842 1000  205    5  127 1034  327  155   57  132 2617   62
 2234  264  714  215 1220  728   64  209  740 1284 1224 1228  546  217
 1109 1018  559  195  467 1041  186  497   60 1069 1071  199  646  647
 1474   92 1014  575  210  711 1092  754   48  768] [ 246 1475  338  528 1200  434  977  743   78  975   44] [ 110  218 16

[  97 1631  851  719  175 1297  571   44  104  206  556  799   55   57
  601 1546  198  139  803  381 1308   13 1389  714   64  755  562   84
   22  186  631  633  614  615 1194   43  199 1107  669  177 1310 3029
  134 1173  565  210  711  183] [1623  648   88 1355  723  111   19  164  403] [ 176  695  213  770 1210 1835 1200 1042   50 1061    5  168   40 1454
  124  434]
[  82  648  266 2622   44  206   18 1396  601 1042  214 2101  178  405
 1546 1462 1623  198 1487 1712 2061  429  381  695 1148 2599  770  170
   84  597 1344 1346 1887 3508  199  723  565] [2351 1254  134  732] [2920 1597  600  614 2498  403  144 2326 2235  184   50]
[2320  237  558  240  872 1165  566  567   97   40  573  450  876  255
  256  576  110  123  587  128  588  396 2072  462  278 1536  279  592
  794  595  596 1494 2332  207  401 1045  612 1617  864  620   76  841
  623 1460  625 1253  629  630 1192 1448  632 1728  321 1351 2738 1258
 1766  114 1195 2873  420  540  338    2  645  648 2862    9 1200 1770
  

[ 567   97  110  115  123  587  128  278 2268  794  967  864  841  625
  629 1351  420  342  153  661  662 1072 1629  676 1271 1560 1393  122
  692  274  693  458 1405  709  719 1425 1433  423 1706  156 2762  776
  175 2098  515 1336  792    7   96   44  499  890 2616 1136  845 1557
  374  222  386   79  244  104  277  702 1576  204  720  727  206   69
 1673 2025  917  424  767  771 1998 2353   73 2066  578  579  580 2535
  124 1241  591 1301 1182 1185 1187  799  316   74 2796 1552  155 2525
  125  201 1574 2416 1003  748  538  857  488 1837 1007  763 1458 1529
 1330 1236  394 1531  132  520  601  291  605  167  315 1348 1256  491
  328  198 1963 1730  140 1064  145  657 1967   41 1270  168  375  171
  979  242 1566  868 1567  259  264 1397  695  431 2235  714 1406 1475
  994   47  216 1466  728   64  208   67 1158  434 1228 2011 1105  766
 1586  546  770  217 1018   52  174  218  236  562 1115 2793   84  517
  192  839  861  116  194   22 1539 1041  597  610  611 1344    6  797
 2540 

C:\Users\leero\AppData\Local\Temp/ipykernel_6536/3960466767.py:23: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  np.save('./user_train_like.npy', np.array(user_train_like))
C:\Users\leero\AppData\Local\Temp/ipykernel_6536/3960466767.py:24: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  np.save('./user_vali_like.npy', np.array(user_vali_like))
C:\Users\leero\AppData\Local\Temp/ipykernel_6536/3960466767.py:25: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with differe

In [23]:
train_df.to_csv('./train_df.csv', index=False)
vali_df.to_csv('./vali_df.csv', index=False)
test_df.to_csv('./test_df.csv', index=False)

In [24]:
item_df.reset_index(drop=True, inplace=True)
movie_df = item_df.copy()
item_df.drop(columns=['title', 'genres'], inplace=True)
item_df.to_csv('./item_df.csv', index=False)
movie_df.to_csv('./movie_df.csv', index=False)

In [25]:
with open('./info.pkl', 'wb') as f:
    pickle.dump({'num_user': num_user, 'num_item': num_item}, f)